In [5]:
import numpy as np

class Tensor (object):
    
    def __init__(self,data,
                 autograd=False,
                 creators=None,
                 creation_op=None,
                 id=None):
        
        self.data = np.array(data)
        self.autograd = autograd
        self.grad = None

        if(id is None):
            self.id = np.random.randint(0,1000000000)
        else:
            self.id = id
        
        self.creators = creators
        self.creation_op = creation_op
        self.children = {}
        
        if(creators is not None):
            for c in creators:
                if(self.id not in c.children):
                    c.children[self.id] = 1
                else:
                    c.children[self.id] += 1

    def all_children_grads_accounted_for(self):
        for id,cnt in self.children.items():
            if(cnt != 0):
                return False
        return True 
        
    def backward(self,grad=None, grad_origin=None):
        if(self.autograd):
 
            if(grad is None):
                grad = Tensor(np.ones_like(self.data))

            if(grad_origin is not None):
                if(self.children[grad_origin.id] == 0):
                    return
                    print(self.id)
                    print(self.creation_op)
                    print(len(self.creators))
                    for c in self.creators:
                        print(c.creation_op)
                    raise Exception("cannot backprop more than once")
                else:
                    self.children[grad_origin.id] -= 1

            if(self.grad is None):
                self.grad = grad
            else:
                self.grad += grad
            
            # grads must not have grads of their own
            assert grad.autograd == False
            
            # only continue backpropping if there's something to
            # backprop into and if all gradients (from children)
            # are accounted for override waiting for children if
            # "backprop" was called on this variable directly
            if(self.creators is not None and 
               (self.all_children_grads_accounted_for() or 
                grad_origin is None)):

                if(self.creation_op == "add"):
                    self.creators[0].backward(self.grad, self)
                    self.creators[1].backward(self.grad, self)
                    
                if(self.creation_op == "sub"):
                    self.creators[0].backward(Tensor(self.grad.data), self)
                    self.creators[1].backward(Tensor(self.grad.__neg__().data), self)

                if(self.creation_op == "mul"):
                    new = self.grad * self.creators[1]
                    self.creators[0].backward(new , self)
                    new = self.grad * self.creators[0]
                    self.creators[1].backward(new, self)                    
                    
                if(self.creation_op == "mm"):
                    c0 = self.creators[0]
                    c1 = self.creators[1]
                    new = self.grad.mm(c1.transpose())
                    c0.backward(new)
                    new = self.grad.transpose().mm(c0).transpose()
                    c1.backward(new)
                    
                if(self.creation_op == "transpose"):
                    self.creators[0].backward(self.grad.transpose())

                if("sum" in self.creation_op):
                    dim = int(self.creation_op.split("_")[1])
                    self.creators[0].backward(self.grad.expand(dim,
                                                               self.creators[0].data.shape[dim]))

                if("expand" in self.creation_op):
                    dim = int(self.creation_op.split("_")[1])
                    self.creators[0].backward(self.grad.sum(dim))
                    
                if(self.creation_op == "neg"):
                    self.creators[0].backward(self.grad.__neg__())
                    
                if(self.creation_op == "sigmoid"):
                    ones = Tensor(np.ones_like(self.grad.data))
                    self.creators[0].backward(self.grad * (self * (ones - self)))
                
                if(self.creation_op == "tanh"):
                    ones = Tensor(np.ones_like(self.grad.data))
                    self.creators[0].backward(self.grad * (ones - (self * self)))
                
                if(self.creation_op == "index_select"):
                    new_grad = np.zeros_like(self.creators[0].data)
                    indices_ = self.index_select_indices.data.flatten()
                    grad_ = grad.data.reshape(len(indices_), -1)
                    for i in range(len(indices_)):
                        new_grad[indices_[i]] += grad_[i]
                    self.creators[0].backward(Tensor(new_grad))
                    
                if(self.creation_op == "cross_entropy"):
                    dx = self.softmax_output - self.target_dist
                    self.creators[0].backward(Tensor(dx))
                    
    def __add__(self, other):
        if(self.autograd and other.autograd):
            return Tensor(self.data + other.data,
                          autograd=True,
                          creators=[self,other],
                          creation_op="add")
        return Tensor(self.data + other.data)

    def __neg__(self):
        if(self.autograd):
            return Tensor(self.data * -1,
                          autograd=True,
                          creators=[self],
                          creation_op="neg")
        return Tensor(self.data * -1)
    
    def __sub__(self, other):
        if(self.autograd and other.autograd):
            return Tensor(self.data - other.data,
                          autograd=True,
                          creators=[self,other],
                          creation_op="sub")
        return Tensor(self.data - other.data)
    
    def __mul__(self, other):
        if(self.autograd and other.autograd):
            return Tensor(self.data * other.data,
                          autograd=True,
                          creators=[self,other],
                          creation_op="mul")
        return Tensor(self.data * other.data)    

    def sum(self, dim):
        if(self.autograd):
            return Tensor(self.data.sum(dim),
                          autograd=True,
                          creators=[self],
                          creation_op="sum_"+str(dim))
        return Tensor(self.data.sum(dim))
    
    def expand(self, dim,copies):

        trans_cmd = list(range(0,len(self.data.shape)))
        trans_cmd.insert(dim,len(self.data.shape))
        new_data = self.data.repeat(copies).reshape(list(self.data.shape) + [copies]).transpose(trans_cmd)
        
        if(self.autograd):
            return Tensor(new_data,
                          autograd=True,
                          creators=[self],
                          creation_op="expand_"+str(dim))
        return Tensor(new_data)
    
    def transpose(self):
        if(self.autograd):
            return Tensor(self.data.transpose(),
                          autograd=True,
                          creators=[self],
                          creation_op="transpose")
        
        return Tensor(self.data.transpose())
    
    def mm(self, x):
        if(self.autograd):
            return Tensor(self.data.dot(x.data),
                          autograd=True,
                          creators=[self,x],
                          creation_op="mm")
        return Tensor(self.data.dot(x.data))
    
    def sigmoid(self):
        if(self.autograd):
            return Tensor(1 / (1 + np.exp(-self.data)),
                          autograd=True,
                          creators=[self],
                          creation_op="sigmoid")
        return Tensor(1 / (1 + np.exp(-self.data)))

    def tanh(self):
        if(self.autograd):
            return Tensor(np.tanh(self.data),
                          autograd=True,
                          creators=[self],
                          creation_op="tanh")
        return Tensor(np.tanh(self.data))
    
    def index_select(self, indices):

        if(self.autograd):
            new = Tensor(self.data[indices.data],
                         autograd=True,
                         creators=[self],
                         creation_op="index_select")
            new.index_select_indices = indices
            return new
        return Tensor(self.data[indices.data])
    
    def softmax(self):
        temp = np.exp(self.data)
        softmax_output = temp / np.sum(temp,
                                       axis=len(self.data.shape)-1,
                                       keepdims=True)
        return softmax_output
    
    def cross_entropy(self, target_indices):

        temp = np.exp(self.data)
        softmax_output = temp / np.sum(temp,
                                       axis=len(self.data.shape)-1,
                                       keepdims=True)
        
        t = target_indices.data.flatten()
        p = softmax_output.reshape(len(t),-1)
        target_dist = np.eye(p.shape[1])[t]
        loss = -(np.log(p) * (target_dist)).sum(1).mean()
    
        if(self.autograd):
            out = Tensor(loss,
                         autograd=True,
                         creators=[self],
                         creation_op="cross_entropy")
            out.softmax_output = softmax_output
            out.target_dist = target_dist
            return out

        return Tensor(loss)
        
    
    def __repr__(self):
        return str(self.data.__repr__())
    
    def __str__(self):
        return str(self.data.__str__())  

class Layer(object):
    
    def __init__(self):
        self.parameters = list()
        
    def get_parameters(self):
        return self.parameters

    
class SGD(object):
    
    def __init__(self, parameters, alpha=0.1):
        self.parameters = parameters
        self.alpha = alpha
    
    def zero(self):
        for p in self.parameters:
            p.grad.data *= 0
        
    def step(self, zero=True):
        
        for p in self.parameters:
            
            p.data -= p.grad.data * self.alpha
            
            if(zero):
                p.grad.data *= 0


class Linear(Layer):

    def __init__(self, n_inputs, n_outputs, bias=True):
        super().__init__()
        
        self.use_bias = bias
        
        W = np.random.randn(n_inputs, n_outputs) * np.sqrt(2.0/(n_inputs))
        self.weight = Tensor(W, autograd=True)
        if(self.use_bias):
            self.bias = Tensor(np.zeros(n_outputs), autograd=True)
        
        self.parameters.append(self.weight)
        
        if(self.use_bias):        
            self.parameters.append(self.bias)

    def forward(self, input):
        if(self.use_bias):
            return input.mm(self.weight)+self.bias.expand(0,len(input.data))
        return input.mm(self.weight)


class Sequential(Layer):
    
    def __init__(self, layers=list()):
        super().__init__()
        
        self.layers = layers
    
    def add(self, layer):
        self.layers.append(layer)
        
    def forward(self, input):
        for layer in self.layers:
            input = layer.forward(input)
        return input
    
    def get_parameters(self):
        params = list()
        for l in self.layers:
            params += l.get_parameters()
        return params


class Embedding(Layer):
    
    def __init__(self, vocab_size, dim):
        super().__init__()
        
        self.vocab_size = vocab_size
        self.dim = dim
        
        # this random initialiation style is just a convention from word2vec
        self.weight = Tensor((np.random.rand(vocab_size, dim) - 0.5) / dim, autograd=True)
        
        self.parameters.append(self.weight)
    
    def forward(self, input):
        return self.weight.index_select(input)


class Tanh(Layer):
    def __init__(self):
        super().__init__()
    
    def forward(self, input):
        return input.tanh()


class Sigmoid(Layer):
    def __init__(self):
        super().__init__()
    
    def forward(self, input):
        return input.sigmoid()
    

class CrossEntropyLoss(object):
    
    def __init__(self):
        super().__init__()
    
    def forward(self, input, target):
        return input.cross_entropy(target)

    
class RNNCell(Layer):
    
    def __init__(self, n_inputs, n_hidden, n_output, activation='sigmoid'):
        super().__init__()

        self.n_inputs = n_inputs
        self.n_hidden = n_hidden
        self.n_output = n_output
        
        if(activation == 'sigmoid'):
            self.activation = Sigmoid()
        elif(activation == 'tanh'):
            self.activation == Tanh()
        else:
            raise Exception("Non-linearity not found")

        self.w_ih = Linear(n_inputs, n_hidden)
        self.w_hh = Linear(n_hidden, n_hidden)
        self.w_ho = Linear(n_hidden, n_output)
        
        self.parameters += self.w_ih.get_parameters()
        self.parameters += self.w_hh.get_parameters()
        self.parameters += self.w_ho.get_parameters()        
    
    def forward(self, input, hidden):
        from_prev_hidden = self.w_hh.forward(hidden)
        combined = self.w_ih.forward(input) + from_prev_hidden
        new_hidden = self.activation.forward(combined)
        output = self.w_ho.forward(new_hidden)
        return output, new_hidden
    
    def init_hidden(self, batch_size=1):
        return Tensor(np.zeros((batch_size,self.n_hidden)), autograd=True)
    
class LSTMCell(Layer):
    
    def __init__(self, n_inputs, n_hidden, n_output):
        super().__init__()

        self.n_inputs = n_inputs
        self.n_hidden = n_hidden
        self.n_output = n_output

        self.xf = Linear(n_inputs, n_hidden)
        self.xi = Linear(n_inputs, n_hidden)
        self.xo = Linear(n_inputs, n_hidden)        
        self.xc = Linear(n_inputs, n_hidden)        
        
        self.hf = Linear(n_hidden, n_hidden, bias=False)
        self.hi = Linear(n_hidden, n_hidden, bias=False)
        self.ho = Linear(n_hidden, n_hidden, bias=False)
        self.hc = Linear(n_hidden, n_hidden, bias=False)        
        
        self.w_ho = Linear(n_hidden, n_output, bias=False)
        
        self.parameters += self.xf.get_parameters()
        self.parameters += self.xi.get_parameters()
        self.parameters += self.xo.get_parameters()
        self.parameters += self.xc.get_parameters()

        self.parameters += self.hf.get_parameters()
        self.parameters += self.hi.get_parameters()        
        self.parameters += self.ho.get_parameters()        
        self.parameters += self.hc.get_parameters()                
        
        self.parameters += self.w_ho.get_parameters()        
    
    def forward(self, input, hidden):
        
        prev_hidden = hidden[0]        
        prev_cell = hidden[1]
        
        f = (self.xf.forward(input) + self.hf.forward(prev_hidden)).sigmoid()
        i = (self.xi.forward(input) + self.hi.forward(prev_hidden)).sigmoid()
        o = (self.xo.forward(input) + self.ho.forward(prev_hidden)).sigmoid()        
        g = (self.xc.forward(input) + self.hc.forward(prev_hidden)).tanh()        
        c = (f * prev_cell) + (i * g)

        h = o * c.tanh()
        
        output = self.w_ho.forward(h)
        return output, (h, c)
    
    def init_hidden(self, batch_size=1):
        init_hidden = Tensor(np.zeros((batch_size,self.n_hidden)), autograd=True)
        init_cell = Tensor(np.zeros((batch_size,self.n_hidden)), autograd=True)
        init_hidden.data[:,0] += 1
        init_cell.data[:,0] += 1
        return (init_hidden, init_cell)

In [6]:
import sys,random,math
from collections import Counter
import numpy as np
import sys

np.random.seed(0)

# dataset from http://karpathy.github.io/2015/05/21/rnn-effectiveness/
f = open('shakespear.txt','r')
raw = f.read()
f.close()

vocab = list(set(raw))
word2index = {}
for i,word in enumerate(vocab):
    word2index[word]=i
indices = np.array(list(map(lambda x:word2index[x], raw)))

embed = Embedding(vocab_size=len(vocab),dim=512)
model = LSTMCell(n_inputs=512, n_hidden=512, n_output=len(vocab))
model.w_ho.weight.data *= 0

criterion = CrossEntropyLoss()
optim = SGD(parameters=model.get_parameters() + embed.get_parameters(), alpha=0.05)

def generate_sample(n=30, init_char=' '):
    s = ""
    hidden = model.init_hidden(batch_size=1)
    input = Tensor(np.array([word2index[init_char]]))
    for i in range(n):
        rnn_input = embed.forward(input)
        output, hidden = model.forward(input=rnn_input, hidden=hidden)
#         output.data *= 25
#         temp_dist = output.softmax()
#         temp_dist /= temp_dist.sum()

#         m = (temp_dist > np.random.rand()).argmax()
        m = output.data.argmax()
        c = vocab[m]
        input = Tensor(np.array([m]))
        s += c
    return s

batch_size = 16
bptt = 25
n_batches = int((indices.shape[0] / (batch_size)))

trimmed_indices = indices[:n_batches*batch_size]
batched_indices = trimmed_indices.reshape(batch_size, n_batches).transpose()

input_batched_indices = batched_indices[0:-1]
target_batched_indices = batched_indices[1:]

n_bptt = int(((n_batches-1) / bptt))
input_batches = input_batched_indices[:n_bptt*bptt].reshape(n_bptt,bptt,batch_size)
target_batches = target_batched_indices[:n_bptt*bptt].reshape(n_bptt, bptt, batch_size)
min_loss = 1000

In [11]:
def train(iterations=400):
    global min_loss
    for iter in range(iterations):
        total_loss = 0
        n_loss = 0

        hidden = model.init_hidden(batch_size=batch_size)
        batches_to_train = len(input_batches)
    #     batches_to_train = 32
        for batch_i in range(batches_to_train):

            hidden = (Tensor(hidden[0].data, autograd=True), Tensor(hidden[1].data, autograd=True))

            losses = list()
            for t in range(bptt):
                input = Tensor(input_batches[batch_i][t], autograd=True)
                rnn_input = embed.forward(input=input)
                output, hidden = model.forward(input=rnn_input, hidden=hidden)

                target = Tensor(target_batches[batch_i][t], autograd=True)    
                batch_loss = criterion.forward(output, target)

                if(t == 0):
                    losses.append(batch_loss)
                else:
                    losses.append(batch_loss + losses[-1])

            loss = losses[-1]

            loss.backward()
            optim.step()
            total_loss += loss.data / bptt

            epoch_loss = np.exp(total_loss / (batch_i+1))
            if(epoch_loss < min_loss):
                min_loss = epoch_loss
                print()

            log = "\r Iter:" + str(iter)
            log += " - Alpha:" + str(optim.alpha)[0:5]
            log += " - Batch "+str(batch_i+1)+"/"+str(len(input_batches))
            log += " - Min Loss:" + str(min_loss)[0:5]
            log += " - Loss:" + str(epoch_loss)
            if(batch_i == 0):
                log += " - " + generate_sample(n=70, init_char='T').replace("\n"," ")
            if(batch_i % 1 == 0):
                sys.stdout.write(log)
        optim.alpha *= 0.99
    #     print()

In [12]:
train(10)


 Iter:0 - Alpha:0.05 - Batch 3/249 - Min Loss:61.75 - Loss:61.81766957976234 -                                                                       
 Iter:0 - Alpha:0.05 - Batch 4/249 - Min Loss:61.73 - Loss:61.73141809419138
 Iter:0 - Alpha:0.05 - Batch 5/249 - Min Loss:61.54 - Loss:61.54359421348108
 Iter:0 - Alpha:0.05 - Batch 6/249 - Min Loss:61.16 - Loss:61.1671171211488
 Iter:0 - Alpha:0.05 - Batch 7/249 - Min Loss:60.53 - Loss:60.53046842540566
 Iter:0 - Alpha:0.05 - Batch 8/249 - Min Loss:59.04 - Loss:59.046843137437655
 Iter:0 - Alpha:0.05 - Batch 9/249 - Min Loss:56.24 - Loss:56.24511357766345
 Iter:0 - Alpha:0.05 - Batch 10/249 - Min Loss:54.48 - Loss:54.48507882278959
 Iter:0 - Alpha:0.05 - Batch 11/249 - Min Loss:52.94 - Loss:52.94095581499291
 Iter:0 - Alpha:0.05 - Batch 12/249 - Min Loss:51.00 - Loss:51.006754557346724
 Iter:0 - Alpha:0.05 - Batch 13/249 - Min Loss:48.44 - Loss:48.441520269261524
 Iter:0 - Alpha:0.05 - Batch 14/249 - Min Loss:47.46 - Loss:47.4635979290

 Iter:0 - Alpha:0.05 - Batch 111/249 - Min Loss:24.83 - Loss:24.836808526402447
 Iter:0 - Alpha:0.05 - Batch 112/249 - Min Loss:24.74 - Loss:24.74121925480149
 Iter:0 - Alpha:0.05 - Batch 113/249 - Min Loss:24.65 - Loss:24.652782304450774
 Iter:0 - Alpha:0.05 - Batch 114/249 - Min Loss:24.59 - Loss:24.591493311034043
 Iter:0 - Alpha:0.05 - Batch 116/249 - Min Loss:24.56 - Loss:24.577831544108516
 Iter:0 - Alpha:0.05 - Batch 117/249 - Min Loss:24.53 - Loss:24.537949397515096
 Iter:0 - Alpha:0.05 - Batch 118/249 - Min Loss:24.44 - Loss:24.448719466476813
 Iter:0 - Alpha:0.05 - Batch 119/249 - Min Loss:24.38 - Loss:24.38183304046578
 Iter:0 - Alpha:0.05 - Batch 120/249 - Min Loss:24.29 - Loss:24.296258791445755
 Iter:0 - Alpha:0.05 - Batch 121/249 - Min Loss:24.21 - Loss:24.21586699224145
 Iter:0 - Alpha:0.05 - Batch 122/249 - Min Loss:24.12 - Loss:24.123144458909483
 Iter:0 - Alpha:0.05 - Batch 123/249 - Min Loss:24.03 - Loss:24.03266987043337
 Iter:0 - Alpha:0.05 - Batch 124/249 - Min L

 Iter:0 - Alpha:0.05 - Batch 216/249 - Min Loss:19.82 - Loss:19.825846520812274
 Iter:0 - Alpha:0.05 - Batch 217/249 - Min Loss:19.80 - Loss:19.800237769252497
 Iter:0 - Alpha:0.05 - Batch 218/249 - Min Loss:19.75 - Loss:19.757727600437875
 Iter:0 - Alpha:0.05 - Batch 219/249 - Min Loss:19.70 - Loss:19.705930338727335
 Iter:0 - Alpha:0.05 - Batch 220/249 - Min Loss:19.68 - Loss:19.68218070850589
 Iter:0 - Alpha:0.05 - Batch 221/249 - Min Loss:19.67 - Loss:19.67325558583462
 Iter:0 - Alpha:0.05 - Batch 222/249 - Min Loss:19.64 - Loss:19.64118250473326
 Iter:0 - Alpha:0.05 - Batch 223/249 - Min Loss:19.60 - Loss:19.60889704880078
 Iter:0 - Alpha:0.05 - Batch 224/249 - Min Loss:19.57 - Loss:19.57906048415093
 Iter:0 - Alpha:0.05 - Batch 225/249 - Min Loss:19.54 - Loss:19.547187957921384
 Iter:0 - Alpha:0.05 - Batch 226/249 - Min Loss:19.51 - Loss:19.51051672605764
 Iter:0 - Alpha:0.05 - Batch 227/249 - Min Loss:19.48 - Loss:19.482684270472785
 Iter:0 - Alpha:0.05 - Batch 228/249 - Min Los

 Iter:6 - Alpha:0.047 - Batch 2/249 - Min Loss:11.02 - Loss:11.218418397968417 - hent therseres, and seat therseres, and seat therseres, and seat thers
 Iter:6 - Alpha:0.047 - Batch 3/249 - Min Loss:10.86 - Loss:10.86059981189415
 Iter:6 - Alpha:0.047 - Batch 4/249 - Min Loss:10.84 - Loss:10.841587153534922
 Iter:6 - Alpha:0.047 - Batch 211/249 - Min Loss:10.73 - Loss:10.738971855559084
 Iter:6 - Alpha:0.047 - Batch 212/249 - Min Loss:10.73 - Loss:10.734215108114222
 Iter:6 - Alpha:0.047 - Batch 213/249 - Min Loss:10.72 - Loss:10.728017671973712
 Iter:6 - Alpha:0.047 - Batch 214/249 - Min Loss:10.72 - Loss:10.727355666102655
 Iter:6 - Alpha:0.047 - Batch 215/249 - Min Loss:10.71 - Loss:10.718460780007609
 Iter:6 - Alpha:0.047 - Batch 217/249 - Min Loss:10.71 - Loss:10.711445184870303
 Iter:6 - Alpha:0.047 - Batch 218/249 - Min Loss:10.70 - Loss:10.705591002953534
 Iter:6 - Alpha:0.047 - Batch 221/249 - Min Loss:10.69 - Loss:10.697050374424878
 Iter:6 - Alpha:0.047 - Batch 222/249 - Min

## 출력의 샘플
다음 코드는 모델을 이용해서 예측을 수행하는 학습 논리의 일부를 사용합니다. 문자열 안에 예측결과를 저장하고 문자열 버전의 출력을 함수에 반환합니다.

In [22]:
def generate_sample(n=30, init_char=' '):
    s = ""
    hidden = model.init_hidden(batch_size=1)
    input = Tensor(np.array([word2index[init_char]]))
    print(word2index[init_char])
    print("=================")
    
    for i in range(n):
        print(i)
        print('++++')
        rnn_input = embed.forward(input) #'\n'의 임베딩을 인덱싱
        print("rnn_input : ",rnn_input)
        print()
        output, hidden = model.forward(input=rnn_input, hidden=hidden) # 위에서 학습한 모델 기반으로 순전파(다음단어 예측)
        print("output : ",output)
        print()
        output.data *= 15
        temp_dist = output.softmax()
        temp_dist /= temp_dist.sum()

#         m = (temp_dist > np.random.rand()).argmax() # sample from predictions
        m = output.data.argmax() # take the max prediction
        c = vocab[m]
        print("voca :",c)
        input = Tensor(np.array([m]))
        s += c
    print(len(s))
    print("=========================================================")
    return s

print(generate_sample(n=500, init_char='\n'))

57
0
++++
rnn_input :  [[-3.08088889e-01 -1.14657694e-01 -1.20447462e-02 -1.44470289e-02
   2.83142066e-01 -1.50433224e-01  1.55301157e-01  1.97993167e-02
   1.89416779e-01 -1.29883059e-01 -1.20976711e-01 -2.54145627e-01
   2.48086002e-01  1.36552666e-01  1.20934900e-01 -1.48151350e-01
   4.33932062e-02  1.57699563e-01 -4.82169511e-02 -6.34065729e-02
  -5.89839648e-02  5.59149999e-03  1.32527969e-01 -5.91119849e-02
  -1.77459394e-01  2.58243039e-01  7.42867576e-02  4.00107984e-01
  -1.09410313e-01  3.95830217e-01  7.37227598e-02 -3.44888032e-02
   6.01103862e-02  6.87021830e-02  2.72389574e-01  1.91618772e-01
   9.23266525e-02  1.41260502e-02  3.18811577e-01  3.61730535e-02
   1.50563696e-01  1.95715444e-01 -7.49430597e-02  9.56120108e-02
   8.58090332e-02  8.62739421e-02 -9.67387557e-02 -2.75725661e-03
   6.98926357e-02 -4.37504399e-02  8.12254783e-02  6.54681437e-02
   1.67359798e-01 -1.43859246e-01 -4.56938522e-02  6.02270145e-02
  -9.47704673e-02  9.17617731e-02 -1.40006003e-02  1.

output :  [[ 2.44473048 -0.96172087 -2.52115019  3.01952947 -1.06478533  2.44221574
   4.14374329 -1.49056235 -0.8671902  -0.74715284  2.56762905 -1.20023085
  -4.67043484 -0.15527001  0.38783608  2.50630563  2.91597766  0.33142123
  -0.69415617  0.93229101 -4.7199696  -3.6064628   2.68306512  1.62504532
  -1.44824242 -0.36281085  1.97743144 -0.24680271 -2.11983794  2.934428
  -1.03871878 -0.93265176  2.65395687 -1.01623224 -1.95173673 -4.76175452
  -0.23813881 -1.78383352  0.83232185 -0.72214027 -2.01097695 -0.18449359
  -3.13318376  0.33607593  2.60820896 -0.64812194 -0.91243957  2.31263444
   0.92124618 -1.39816948  1.78406795  3.70028098  0.78800678  0.38882667
  -1.15041405  3.49282223  3.35758047  0.54352306 -3.86134187 -3.320824
  -1.56379356  2.87454347]]

voca : w
10
++++
rnn_input :  [[-0.32426741 -0.02167906 -0.24080027  0.03136758 -0.208225   -0.03278238
  -0.22001711  0.03776043  0.07011504 -0.11436729  0.0330273   0.05940356
  -0.06684418  0.01648022 -0.09097276  0.139300

output :  [[ 3.94824689 -0.07800603 -3.4142926   2.5109286  -1.59058355  3.06146272
   5.18310391 -2.43586477 -1.62286119 -1.45654829  2.61005144 -1.43040775
  -4.46400386 -1.10518332  2.87212359  3.32161445  2.40241995 -1.45982894
  -1.6269004   2.48657889 -4.75930716 -2.53215628  3.39899148  2.08547716
  -2.15862428 -1.99277174  1.72295898 -0.86349738 -2.53073263  3.83401021
  -2.78849424 -1.41062224  3.77448424 -1.56696342 -3.09883838 -4.85238064
   0.78370299 -0.75594259  0.45052027 -0.58508899 -2.25381942 -1.10991543
  -3.2122897  -0.03345722  3.43621222 -1.02926678 -1.32382357  2.25920628
   2.62738767 -1.77450009  1.5592151   4.82945505 -0.86683224  3.43116622
  -1.40102585  4.13587671  3.39962831  0.28625799 -4.04285005 -3.75632799
  -1.97309653  2.94602422]]

voca : w
18
++++
rnn_input :  [[-0.32426741 -0.02167906 -0.24080027  0.03136758 -0.208225   -0.03278238
  -0.22001711  0.03776043  0.07011504 -0.11436729  0.0330273   0.05940356
  -0.06684418  0.01648022 -0.09097276  0.13

output :  [[ 3.82912396 -0.00792351 -2.90201078  2.55511245 -1.38640139  3.42882204
   5.3979763  -2.02934114 -1.55539707 -1.39166872  2.61200649 -1.82292584
  -4.2150373  -1.22504283  2.35435628  2.89147678  1.46827907 -0.62442529
  -1.67976659  1.79914258 -4.51713831 -3.08260249  2.81500712  2.13973198
  -2.59420997 -1.19458544  2.06409859 -1.07213585 -1.84215958  3.41348884
  -2.23478506 -1.07242551  3.33600815 -0.93501096 -2.36765923 -4.51947297
   1.09594057 -0.3843232  -0.54686185 -0.38516742 -2.1275381  -0.82487429
  -2.70009753 -0.13633841  3.31992974 -1.71844428 -1.10317552  2.45434924
   2.07993059 -1.51020239  2.1610033   4.49273576 -1.55762242  2.93841422
  -1.12984775  4.33996318  2.64746784 -0.72313633 -3.84739148 -3.61923886
  -2.0910275   3.04304807]]

voca : w
33
++++
rnn_input :  [[-0.32426741 -0.02167906 -0.24080027  0.03136758 -0.208225   -0.03278238
  -0.22001711  0.03776043  0.07011504 -0.11436729  0.0330273   0.05940356
  -0.06684418  0.01648022 -0.09097276  0.13

   0.04046833  0.16639315]]

output :  [[ 0.70516875 -1.7136323  -2.57754894  6.05464827 -3.30810059  6.87286542
   2.29680265 -1.57333275 -2.42734338 -4.59777638  4.99024747  0.75874374
  -3.05584945  2.25979046  0.31252563  0.67642977  4.21645508 -1.42974767
  -4.38405515  4.8343544  -4.20040573 -0.3093265   5.21588347  3.69992059
  -2.28027095 -1.04589166  2.78147102 -1.1916336  -2.32734783  0.95919796
  -3.77798944 -1.64317058  2.11965279 -3.78414445 -2.63722584 -3.5511555
  -0.93526225 -1.73417344  2.19869185 -3.14773627 -2.2715423  -2.44419534
  -1.03119739  0.82887376  8.7081558   0.64272456 -3.83857969  4.81996514
  -0.3066099  -2.64599633 -0.76868183  4.60445164  3.12603457 -1.6917784
  -3.57928408  3.30729304  2.19706995  1.89076429 -3.44469256 -3.73278089
  -2.2647681   4.5750454 ]]

voca : i
49
++++
rnn_input :  [[ 1.06333497e-01 -1.71303623e-01  3.05294222e-01 -1.06087896e-01
   3.91634424e-02 -9.09038618e-02 -1.42511682e-01 -4.21854854e-02
  -2.14964228e-02 -6.29787638e-0

...

output :  [[ 0.70516958 -1.71363247 -2.57754982  6.0546487  -3.3081012   6.87286605
   2.29680283 -1.57333344 -2.42734389 -4.59777641  4.99024801  0.75874391
  -3.05584983  2.25979024  0.31252645  0.67643023  4.21645582 -1.42974854
  -4.38405532  4.83435426 -4.20040596 -0.3093262   5.21588425  3.69992121
  -2.28027081 -1.04589235  2.78147192 -1.19163437 -2.32734844  0.95919832
  -3.77799084 -1.64317079  2.11965338 -3.78414588 -2.63722699 -3.55115591
  -0.93526158 -1.73417354  2.19869187 -3.14773692 -2.2715428  -2.44419597
  -1.03119771  0.82887458  8.70815638  0.64272432 -3.83857983  4.81996588
  -0.30660922 -2.64599675 -0.76868251  4.60445235  3.12603441 -1.69177686
  -3.57928431  3.3072935   2.19707066  1.89076504 -3.44469295 -3.73278129
  -2.26476842  4.57504595]]

voca : i
439
++++
rnn_input :  [[ 1.06333497e-01 -1.71303623e-01  3.05294222e-01 -1.06087896e-01
   3.91634424e-02 -9.09038618e-02 -1.42511682e-01 -4.21854854e-02
  -2.14964228e-02 -6.29787638e-02  6.99676732e-02  1.20191

output :  [[ 2.29293709 -2.22264602 -2.7288201   6.84177807 -1.41748864  5.90850783
   4.80229441 -2.24976112 -2.83114444 -3.36615759  5.46154647  0.99717741
  -4.68979548  1.83325061  0.60423428  1.97097105  4.51013127 -0.6903099
  -3.89464432  1.87534703 -4.0472265  -0.75099992  2.03001756  4.90238226
  -0.25231871 -0.91012922  1.99617522 -1.81594445 -3.9521347   3.29226249
  -3.94899748 -2.95861423  6.07632424 -2.59401241 -3.08256917 -4.57614103
   1.64147707 -1.04668997  2.42989209 -3.44677152 -3.12125039 -3.69071127
  -3.25448568  1.09078286  6.76397836  1.92021431 -4.19181513  3.92905653
   1.10787316 -3.34150304 -0.34873212  3.90199829  3.45402091  1.56892864
  -3.63110177  5.85757836 -0.25550534  0.09913207 -4.58493988 -4.87256385
  -3.45056929  3.05622475]]

voca : e
451
++++
rnn_input :  [[-4.79650464e-02 -1.34146243e-01  3.26508559e-01  3.72245737e-01
  -1.96343513e-01  3.22147077e-02 -1.35288278e-02 -2.15375865e-01
   2.71838798e-02 -2.69332640e-03 -2.87036874e-01 -1.837595

output :  [[ 1.4092077  -1.29419569 -4.15757786  5.04482115 -2.57738461  7.47739942
   4.02269645 -1.50214783 -2.44129265 -4.18531363  7.47109754  0.08854838
  -2.58835456  2.10090594 -1.40657368  1.33294403  5.58379706  0.23316905
  -3.94572292  5.76375801 -1.41645123 -1.27925734  0.48951713  5.38718754
  -0.17571264 -0.72500286  3.338588   -2.87220611 -3.04128386  0.17519427
  -3.07328392 -2.04086543  2.13022157 -2.28655445 -2.36182705 -2.31889975
  -0.63154351 -1.01938452  2.16032474 -1.90851089 -3.35854038 -2.68079483
  -0.99145341  0.52319163  6.85705372  0.88451729 -3.95108711  5.76185693
   0.3137407  -2.74937583 -0.02811174  2.1447116   1.26228326 -0.81847091
  -3.08407053  1.44735933 -0.80499395  0.46484369 -2.64136995 -3.09610438
  -2.77862138  2.36340523]]

voca : o
463
++++
rnn_input :  [[ 2.25434498e-01 -2.00502150e-02  2.94608883e-01  4.28714986e-02
   9.53759002e-02  1.04027198e-01  2.85981391e-01 -1.30969607e-01
  -1.49214112e-01  3.16499119e-02  3.54741359e-01 -5.38747

output :  [[-0.56016145  0.39436825 -1.60176466  4.02209122 -3.78088599  0.86238332
   0.12495402 -2.11056032 -1.09510625 -1.91587903 -0.15797288  1.36193776
  -1.15833569  2.1627404   3.80351892  2.34877213  6.28008544 -1.21090537
  -0.5998495   1.19055459 -0.14590951  0.90413219  3.18902136 -1.96951164
   1.10379199 -1.98135808 -1.20948083 -0.89466548 -2.40941363 -1.18283278
  -1.68868882 -1.72758242 -0.21983243 -4.61132771 -2.6236922  -1.14829494
  -1.53379069  0.30029373  3.84329497 -2.48533219 -1.72941727 -2.48573141
   0.18150408  2.83595577  1.48585288  2.14681091 -2.09588795  0.32361343
   0.9309555  -2.46969528 -0.48952013  2.61606482  5.69682535 -0.28474859
  -2.28842947  1.8481081   3.52473145  2.30263322 -1.20020452 -2.87965461
  -1.85982345  2.02125137]]

voca :  
476
++++
rnn_input :  [[ 0.03733748 -0.2673653   0.16828547  0.13860829  0.05174873 -0.08139417
   0.05741333  0.10724653  0.30500353  0.0748281  -0.20957163  0.03485307
  -0.05738206 -0.04429936 -0.14492247  0.0

output :  [[ 1.74906453 -1.31247368 -0.52672547  2.6496846  -2.10146789  3.0394656
  -1.34286757 -2.47325342 -0.55620907 -0.9044989   0.3349946  -2.9145355
  -1.3817449  -2.31444359  0.93216786  3.79071579 -0.67307636 -1.77124824
  -1.91708433  3.41203121 -0.23965604 -2.78486244  6.44954455  0.51355686
  -1.09461525 -0.8848971  -0.66808591 -1.45032335 -0.44336793  1.0128408
  -1.62760536  0.22729292  0.91591465 -0.01486978 -0.53609887 -1.60131726
   1.72102198 -2.12719976 -2.27784105  0.15596038 -1.14681157  0.22416198
   0.04476441 -0.86092638  2.48227053 -2.1616127  -1.58175     1.66190587
   0.66247159  0.64682406 -1.31296552  4.16068652 -0.93424478  2.73668912
  -0.60369751  4.0050622   2.78662435 -1.39479526 -2.10488128 -2.86800188
  -1.29800468  5.89234362]]

voca : n
490
++++
rnn_input :  [[-7.11298679e-02  1.77079345e-02 -5.97550035e-02  2.34228650e-01
  -3.91664750e-02 -2.81774532e-01  1.74511781e-01  1.73700389e-01
   2.81626948e-01  6.08077259e-02 -5.25296834e-02  1.06771289

## 소멸하는 기울기, 폭발하는 기울기

이 신경망에는 추가적인 비선형성이 은닉 상태 생성 절차에 추가되었습니다. 그러므로 순전파는 다음 3단계를 거칩니다.  
1. 이전 은닉상태와 가중치 행렬과의 행렬 곱  
2. 다음 단어의 임베딩과의 덧셈
3. 비선형성 적용(activation function)
이 비선형성은 신경망의 안정성에 중요한 역할을 합니다. 단어 시퀸스 길이와 관계없이(이론적으로는 시간이 지날수록 계속 커지는)은닉 상태는 비선형성의 값(sigmoid 의 경우 0 또는 1)사이에 머물도록 강제당합니다.  
.  
하지만 이렇게 좋은 속성을 가지지 못한 역전파는 순전파와는 약간 다른 방식으로 일어납니다.  
.  
역전파는 극단적으로 크거나 극단적으로 작은 값으로 이어지는 경향이 있습니다. 큰 값은 발산(수많은 not-a-number[NaN])을 유발하며, 극도로 작은값은 신경망이 학습하지 못하게 만듭니다.